In [1]:
import json

In [2]:
from mlscorecheck.symbolic import get_base_objects, ProblemSolver, get_all_objects, get_objects_without_complements, solve_func
from mlscorecheck.individual import Solution, Solutions
from mlscorecheck.scores import *

import datetime

import logging
logger = logging.getLogger('mlscorecheck')
#logger.setLevel(logging.WARNING)

In [3]:
from mlscorecheck.individual import load_solutions

In [14]:
scores = get_objects_without_complements(algebraic_system='sympy')

In [15]:
algebra = scores['acc'].get_algebra()
symbols = scores['acc'].symbols

In [5]:
print(scores.keys())

dict_keys(['acc', 'sens', 'spec', 'ppv', 'npv', 'fbp', 'f1p', 'fbm', 'f1m', 'gm', 'fm', 'upm', 'mk', 'lrp', 'lrn', 'bm', 'pt', 'dor', 'ji', 'bacc', 'kappa', 'p4', 'mcc'])


In [6]:
soljson = {'solutions': []}

solutions = []
start_idx = 0
for idx, score0 in enumerate(list(scores.keys())):
    if idx < start_idx:
        continue
    for score1 in list(scores.keys())[(idx+1):]:
        if (score0, score1) in [('upm', 'mk'), ('upm', 'p4'), ('upm', 'mcc'), ('mk', 'p4'), ('mk', 'mcc'), ('bm', 'bacc'), ('p4', 'mcc')]:
            continue
        #print(datetime.datetime.now(), score0, score1)
        ps = ProblemSolver(score0=scores[score0], score1=scores[score1])
        ps.solve(implicit=False, check=False)
        ps.edge_cases()
        soljson['solutions'].append(ps.get_solution().to_dict())
        #soljson['solutions'].append({'scores': [score0, score1],
        #                                'solutions': ps.raw_solutions})
        #if len(ps.raw_solutions) > 0:
        #    print(ps.raw_solutions[0]['tp'], flush=True)
        #else:
        #    print('EMPTY', flush=True)
        #solutions.append(ps)

2023-09-09 13:48:59,475:INFO:solving acc sens
2023-09-09 13:49:00,799:INFO:solved
2023-09-09 13:49:00,801:INFO:solving acc spec
2023-09-09 13:49:01,818:INFO:solved
2023-09-09 13:49:01,819:INFO:solving acc ppv
2023-09-09 13:49:03,585:INFO:solved
2023-09-09 13:49:03,587:INFO:solving acc npv
2023-09-09 13:49:05,047:INFO:solved
2023-09-09 13:49:05,049:INFO:solving acc fbp
2023-09-09 13:49:06,636:INFO:solved
2023-09-09 13:49:06,644:INFO:solving acc f1p
2023-09-09 13:49:07,897:INFO:solved
2023-09-09 13:49:07,899:INFO:solving acc fbm
2023-09-09 13:49:09,401:INFO:solved
2023-09-09 13:49:09,407:INFO:solving acc f1m
2023-09-09 13:49:10,947:INFO:solved
2023-09-09 13:49:10,950:INFO:solving acc gm
2023-09-09 13:49:12,434:INFO:solved
2023-09-09 13:49:12,477:INFO:solving acc fm
2023-09-09 13:49:14,487:INFO:solved
2023-09-09 13:49:14,520:INFO:solving acc upm
2023-09-09 13:49:17,716:INFO:solved
2023-09-09 13:49:17,764:INFO:solving acc mk
2023-09-09 13:49:20,692:INFO:solved
2023-09-09 13:49:20,779:INFO:

In [7]:
soljson

{'solutions': [{'scores': ['acc', 'sens'],
   'solutions': [{'solution': {'tn': {'expression': 'acc*n + acc*p - p*sens',
       'symbols': ['acc', 'n', 'p', 'sens']},
      'tp': {'expression': 'p*sens', 'symbols': ['p', 'sens']}},
     'conditions': []}]},
  {'scores': ['acc', 'spec'],
   'solutions': [{'solution': {'tp': {'expression': 'acc*n + acc*p - n*spec',
       'symbols': ['acc', 'n', 'p', 'spec']},
      'tn': {'expression': 'n*spec', 'symbols': ['n', 'spec']}},
     'conditions': []}]},
  {'scores': ['acc', 'ppv'],
   'solutions': [{'solution': {'tp': {'expression': '(acc*n + acc*p - n)*ppv/(2*ppv - 1)',
       'symbols': ['acc', 'n', 'p', 'ppv']},
      'tn': {'expression': '(acc*n*ppv + acc*p*ppv - acc*n - acc*p + n*ppv)/(2*ppv - 1)',
       'symbols': ['acc', 'n', 'p', 'ppv']}},
     'conditions': [{'expression': '2*ppv - 1',
       'symbols': ['ppv'],
       'depth': 1,
       'mode': 'non-zero'}]}]},
  {'scores': ['acc', 'npv'],
   'solutions': [{'solution': {'tp': {'ex

In [8]:
with open('solutions.json', 'wt') as file:
    file.write(json.dumps(soljson).replace('^', '**'))

In [16]:
with open('solutions.json', 'rt') as file:
    soljson = json.load(file)

In [17]:
non_negatives = []
for idx in range(len(soljson['solutions'])):
    sol = soljson['solutions'][idx]['solutions']
    for jdx in range(len(sol)):
        nneg = sol[jdx]['conditions']
        for kdx in range(len(nneg)):
            if nneg[kdx]['mode'] == 'non-negative':
                non_negatives.append(nneg[kdx]['expression'])

In [18]:
non_negatives = list(set(non_negatives))

In [19]:
len(non_negatives)

161

In [25]:
params = {'p': symbols.p,
            'n': symbols.n,
            'tp': symbols.tp,
            'tn': symbols.tn}
gm = geometric_mean_standardized(**params, sqrt=algebra.algebra.sqrt)
mk = markedness_standardized(**params)
dor = diagnostic_odds_ratio_standardized(**params)
kappa = cohens_kappa_standardized(**params)
params['gm'] = gm
params['mk'] = mk
params['dor'] = dor
params['kappa'] = kappa
params['sqrt'] = algebra.algebra.sqrt

In [35]:
symb = eval(non_negatives[1], {'kappa': sp.Symbol('kappa'), 'dor': sp.Symbol('dor'), 'p': sp.Symbol('p'), 'n': sp.Symbol('n')})

In [37]:
sp.simplify(symb)

kappa**2*n**4 + kappa**2*p**4 - 4*kappa*n**3*p*(dor - 1) - 4*kappa*n*p**3*(dor - 1) + 2*n**2*p**2*(2*dor**2 - 4*dor*kappa*(dor - 1) - 4*dor + kappa**2*(2*dor**2 - 4*dor + 1) + 2)

In [26]:
result = eval(non_negatives[1].replace('^', '**'), params)

In [27]:
result

n**4*(-2*n*p + 2*n*tp + 2*p*tn)**2/(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp)**2 - n**3*p*(4*tn*tp/((n - tn)*(p - tp)) - 4)*(-2*n*p + 2*n*tp + 2*p*tn)/(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp) + n**2*p**2*(4*tn**2*tp**2/((n - tn)**2*(p - tp)**2) - 8*tn*tp/((n - tn)*(p - tp)) - 2*(4*tn**2*tp**2/((n - tn)**2*(p - tp)**2) - 4*tn*tp/((n - tn)*(p - tp)))*(-2*n*p + 2*n*tp + 2*p*tn)/(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp) + 2*(-2*n*p + 2*n*tp + 2*p*tn)**2*(2*tn**2*tp**2/((n - tn)**2*(p - tp)**2) - 4*tn*tp/((n - tn)*(p - tp)) + 1)/(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp)**2 + 4) - n*p**3*(4*tn*tp/((n - tn)*(p - tp)) - 4)*(-2*n*p + 2*n*tp + 2*p*tn)/(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp) + p**4*(-2*n*p + 2*n*tp + 2*p*tn)**2/(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp)**2

In [32]:
import sympy as sp
simple = sp.factor(result)

In [33]:
simple >= 0

4*(n + p)**2*(n*p - n*tp - p*tn)**2*(-n**2*tp + n*tn*tp + p**2*tn - p*tn*tp)**2/((n - tn)**2*(p - tp)**2*(n**2 - n*tn + n*tp + p**2 + p*tn - p*tp)**2) >= 0

In [ ]:
complex(0, 1)

1j

In [ ]:
non_negatives

['-4*gm^2*lrn + 1',
 '16*n^2*p^2*pt^4 - 64*n^2*p^2*pt^3 + 96*n^2*p^2*pt^2 - 64*n^2*p^2*pt + 16*n^2*p^2 + ((n^4 + 8*n^3*p + 14*n^2*p^2 + 8*n*p^3 + p^4)*pt^4 + 9*n^2*p^2 + 10*n*p^3 + p^4 - 4*(3*n^3*p + 11*n^2*p^2 + 9*n*p^3 + p^4)*pt^3 + 2*(3*n^3*p + 29*n^2*p^2 + 29*n*p^3 + 3*p^4)*pt^2 - 4*(9*n^2*p^2 + 10*n*p^3 + p^4)*pt)*upm^2 - 8*((n^3*p + 4*n^2*p^2 + n*p^3)*pt^4 + 3*n^2*p^2 + n*p^3 - 2*(n^3*p + 7*n^2*p^2 + 2*n*p^3)*pt^3 + (n^3*p + 19*n^2*p^2 + 6*n*p^3)*pt^2 - 4*(3*n^2*p^2 + n*p^3)*pt)*upm',
 '16*n^2*ppv^2 + (4*(n^2 + 2*n*p + p^2)*ppv^2 + n^2 + 2*n*p + p^2 + 4*(n^2 - p^2)*ppv)*upm^2 - 8*(2*n^2*ppv^2 + (n^2 + n*p)*ppv)*upm',
 '64*fm^6*p^3 + 288*fm^4*n*p^2 + (3*(18*fm^2 - 11)*n^2*p + 3*(36*fm^2 + 11)*n*p^2 + (54*fm^2 + 1)*p^3 - n^3)*p4^3 - 24*(7*fm^2*n^2*p + 4*fm^2*n*p^2 + fm^2*p^3)*p4^2 - 48*(2*fm^4*p^3 - 3*fm^2*n^2*p + (4*fm^4 + 3*fm^2)*n*p^2)*p4 + 6*sqrt(3)*sqrt(-(256*fm^8*n^2*p^3 + 1024*fm^6*n^3*p^2 + ((fm^2 - 1)*n^5 - (27*fm^4 - 35*fm^2 + 4)*n^4*p - 2*(54*fm^4 - 17*fm^2 + 3)*n^3*p^2 

In [ ]:
with open('solutions.json', 'rt') as file:
    soljson = json.load(file)

In [ ]:
import numpy as np
params = {'p': 20,
            'tp':2,
            'n': 20,
            'tn': 3}

p4 = scores['p4'].function(**params)
dor = scores['dor'].function(**params)

In [ ]:
p4, dor

(0.12060301507537688, 0.0196078431372549)

In [ ]:
def sqrt(value):
    return value**0.5

In [ ]:
params['p4'] = p4
params['dor'] = dor
params['sqrt'] = sqrt

In [ ]:
nz = soljson['solutions'][3]['solutions'][2]['non_zero']
for idx in range(len(nz)):
    print(eval(nz[idx]['expression'], params))

0.014545087245271583
0.9803921568627451
-0.9803921568627451
(14.021934902647263-12.366553223423365j)
0.9611687812379853
(1361.8371078959206-1201.0632764561124j)
(-9.459060005911908-5.086479481880244e-15j)
0.12060301507537688


In [ ]:
nn = soljson['solutions'][3]['solutions'][3]['non_negative']
for idx in range(len(nn)):
    res = eval(nn[idx]['expression'], params)
    print(res)


2
3
6
(0.010296337808206433-1.4673922859032801e-18j)
-18287.01857329078
(154.17142303771368+2.7363060938897773e-14j)
(23120.335145295045-2.661874641536731e-12j)
(-3676.274502992575-5403.099664713109j)
(23120.335145295037-2.1608219223506386e-12j)
(97.12191058873145+9.121020312965925e-15j)


In [ ]:
np.float64((-1))**(1/3)

/tmp/ipykernel_17121/865478692.py:1: RuntimeWarning: invalid value encountered in scalar power
  np.float64((-1))**(1/3)


nan

In [ ]:
for idx in range(4):
    sols = soljson['solutions'][3]['solutions'][idx]['solution']['tn']['expression']
    print(eval(sols, params))

(-0.22746272942966614-1.275415440949301e-15j)
(1.9999999999999383+1.4560339182320445e-16j)
(3.0000000000000013+1.5904901744632495e-15j)
(46.89412939609639-4.606781253371534e-16j)


In [ ]:
symbols = scores['acc'].symbols.to_dict()

In [ ]:

dor_fun = scores['dor'].function(**{'p': symbols['p'],
                                  'n': symbols['n'],
                                  'tp': symbols['tp'],
                                  'tn': symbols['tn']})
ji_fun = scores['ji'].function(**{'p': symbols['p'],
                                  'n': symbols['n'],
                                  'tp': symbols['tp'],
                                  'tn': symbols['tn']})

In [ ]:
par = {**symbols,
        'ji': ji_fun,
        'dor': dor_fun}

In [ ]:
soljson['solutions'][0]['solutions'][0]['non_negative'][0]['expression']

'ji**2*n**2 - 2*((dor - 1)*ji**2 + dor*ji)*n*p + ((dor**2 - 2*dor + 1)*ji**2 + dor**2 - 2*(dor**2 - dor)*ji)*p**2'

In [ ]:
nonneg = soljson['solutions'][0]['solutions'][0]['non_negative'][0]['expression']
nonneg = eval(nonneg, par)

In [ ]:
algebra.simplify(nonneg)

(n^2*p + n*p^2 - 2*n*p*tn + p*tn^2 - n^2*tp - n*p*tp + n*tn*tp)^2*tp^2/((n + p - tn)^2*(n - tn)^2*(p - tp)^2)

In [ ]:
algebra = scores['acc'].symbols.algebra

In [ ]:
algebra.subs(nonneg, {'dor': dor_fun, 'ji': ji_fun})

AttributeError: 'str' object has no attribute 'subs'